# Applied Data Science Capstone - Week 4: Where to open a bar in berlin?

### Content

<ul>
    <li> 1. Introduction </li>
    <li> 2. Data </li>
    <ul>
        <li> 2.1. Preparation of Geo Data </li>
        <li> 2.2. Collection of Venues </li>
    </ul>
    <li> 3. Methodology </li>
    <ul>
        <li> 3.1. Visualization of Query Results (Exploratory Analysis) </li>
        <li> 3.2. Application of Neural Network (Machine Learning) </li>
    </ul>
    <li> 4. Results </li>
    <li> 5. Discussion </li>
    <li> 6. Conclusion </li>
</ul>
   

## 1. Introduction


This capstone project investigates the relationship between bars and other venues in Berlin. More concretely we will search for bars and venues of other categories in each postal code region in Berlin. After some data cleaning and filtering we are going to build a regression model. Thereby the number of bars in each region will serve as dependent variable and the number of venues in certain different categories will serve as independent variable. The regression model is going to be a 1-Layer Neural Network which is very similar to a Linear Problem. The difference will be explained in chapter 2.4. 


Usually regression models are built to predict an entity which was not observed. Instead in this situation the model is used to compute the difference between the predicted and the real number of bars in each region. The intention is to find a region with a lack of bars. Assuming the Neural Network describes a valid relation this could be a region with a high difference of predicted and real number of bars.


Of course if someone want's to open a bar there are a lot of very important factors, which are not inherited in this model - i.e. rent, location (more concret than just the postal code region) and many others. But in the situation if the general region is not determined, this analysis could give a hint which region could be fruitful.

## 2. Data

We start by importing the necessary packages.

In [1]:
import requests
import numpy as np
import pandas as pd
import folium
from geopy.geocoders import Nominatim
import warnings
warnings.filterwarnings('ignore')


### 2.1. Preparation of geo data

The venues will be grouped by postal code regions of berlin. Therefore the information of these areas are imported as a geojson-file from the website 'https://data.technologiestiftung-belrin.de/'.

To read the geojson-file the package geopandas is used. The result is stored in a dataframe. Each line in this dataframe contains the information for one postal code region.

In [74]:
berlin_geojson = 'https://data.technologiestiftung-berlin.de/data/plz/plz.geojson'

import geopandas as gpd

df_berlin_geo = gpd.read_file(berlin_geojson)

In the next step we drop the columns 'gml_id' and 'spatial_name' since they are not needed in the further procedure. Furthermore we add two variables ('Latitude' and 'Longitude') to the dataframe and initialize them with zeros.

In [75]:
df_berlin_geo.drop('gml_id', axis = 1, inplace = True)
df_berlin_geo.set_index('spatial_name', inplace = True)

latitude = np.zeros(shape = (df_berlin_geo.shape[0],))
longitude = np.zeros(shape = (df_berlin_geo.shape[0],))

df_berlin_geo['Latitude'] = latitude
df_berlin_geo['Longitude'] = longitude

The entries in the columns 'Latitude' and 'Longitude' will serve as the coordinates for the queries we are going to send to the Foursquare API. It is therefore reasonable to choose a point in the center of each postal code region. This is done with a heuristic approach in the following code secion.

What does this code in detail? Each postal code region is saved as a polygon in the geodataframe df_berlin_geo. The polygon contains a list of coordinates which bound the concerning region. Here we simply take the average of these boundary coordinates as the center of the region. This procedure does not assure the resulting point to lie in the centre of a postal code region, but it works heuristically in this situation.

In [76]:
import shapely

geolocator = Nominatim(user_agent = 'foursquare_agent')    

for postal_code in df_berlin_geo.index:
    
    polygon = df_berlin_geo.loc[postal_code,'geometry']
    
    #print(postal_code, type(polygon))
    
    # if len(polygon) > 1, the polygon is a multipolygon and therefore
    # the first element (polygon) is chosen
    if(type(polygon) is shapely.geometry.multipolygon.MultiPolygon):
        polygon = polygon[0]
        
    lat = np.mean(polygon.exterior.coords.xy[1])
    lng = np.mean(polygon.exterior.coords.xy[0])
    
    df_berlin_geo.at[postal_code,'Latitude'] = lat
    df_berlin_geo.at[postal_code,'Longitude'] = lng

    

The next code segments plots the postal code regions of Berlin and the center of each region.

In [78]:
geolocator = Nominatim(user_agent = 'foursquare_agent')
location = geolocator.geocode('Berlin, Germany')

berlin_lat = location.latitude
berlin_lng = location.longitude



berlin_map = folium.Map(location = [berlin_lat, berlin_lng],
                        zoom_start = 10,
                        title = 'Berlin Postal Codes')

berlin_map.choropleth(
    geo_data = berlin_geojson)

for lat,lng, pc in zip(df_berlin_geo['Latitude'],
                       df_berlin_geo['Longitude'],
                       df_berlin_geo.index):
    label = folium.Popup(pc, parse_html = True)
    #print(pc,lat,lng)
    folium.CircleMarker(
        [lat, lng],
        radius= 5,
        fill = True,
        popup = label,
        fill_opacity = 0.7).add_to(berlin_map)
    
berlin_map

### 2.2. Collection of venues

Now we can go on with collecting the venues with the Foursquare API. Therefore the Credentials are set in the next code segment. These variables are hidden and need to be set manually.

<b>Notice:</b> It's necessary to have an account at Foursquare which allows to send about 190 queries.

If you cannot reproduce this part of the code you can still take a look at the results in the .html-file (in the same git repository).

In [1]:
# Removed Credentials for the Foursquare API (privacy reasons)

The following code is taken from the previous part of the course. It collects venues around the centre of each postal code region. If the query suceeded for a certain region the region is printed.

In [10]:
venues_list = []

for postal_code in df_berlin_geo.index:
    
    print(postal_code)
    
    request_url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            df_berlin_geo.loc[postal_code,'Latitude'], 
            df_berlin_geo.loc[postal_code,'Longitude'], 
            1000.0, 
            LIMIT)
    
    results = requests.get(request_url).json()['response']['groups'][0]['items']
    
    postal_code_list = list()
    
    for v in results:
        if('postalCode' in v['venue']['location'].keys()):
            postal_code_list.append(v['venue']['location']['postalCode'])
        else:
            postal_code_list.append(postal_code)
    
    venues_list.append([(
            postal_code,
            v['venue']['name'],
            v['venue']['categories'][0]['name'],
            postal_code_elem) for v,postal_code_elem in zip(results,postal_code_list)])



10115
10117
10119
10178
10179
10243
10245
10247
10249
10315
10317
10318
10319
10365
10367
10369
10405
10407
10409
10435
10437
10439
10551
10553
10555
10557
10559
10585
10587
10589
10623
10625
10627
10629
10707
10709
10711
10713
10715
10717
10719
10777
10779
10781
10783
10785
10787
10789
10823
10825
10827
10829
10961
10963
10965
10967
10969
10997
10999
12043
12045
12047
12049
12051
12053
12055
12057
12059
12099
12101
12103
12105
12107
12109
12157
12159
12161
12163
12165
12167
12169
12203
12205
12207
12209
12247
12249
12277
12279
12305
12307
12309
12347
12349
12351
12353
12355
12357
12359
12435
12437
12439
12459
12487
12489
12524
12526
12527
12555
12557
12559
12587
12589
12619
12621
12623
12627
12629
12679
12681
12683
12685
12687
12689
13051
13053
13055
13057
13059
13086
13088
13089
13125
13127
13129
13156
13158
13159
13187
13189
13347
13349
13351
13353
13355
13357
13359
13403
13405
13407
13409
13435
13437
13439
13465
13467
13469
13503
13505
13507
13509
13581
13583
13585
13587
13589
1359

In the next step all venues are saved in a dataframe: With the Foursquare API we just searched venues around the center of each postal code region. The venues which were found in a certain query don't necessarily belong to the concerning postal region. These venues are dropped in a second step. This also ensures that no venue is contained more than once in the dataframe.

In [11]:
venues = pd.DataFrame([
        item for venue_list in venues_list for item in venue_list])

venues.columns = ['postal_code_query',
                  'Name', 'Category',
                  'true_postal_code']
venues = venues.query('postal_code_query == true_postal_code')
venues.drop('postal_code_query', axis = 1, inplace = True)
venues.rename(columns = {'true_postal_code':'postal_code'}, inplace = True)

The resulting dataframe looks as follows.

In [12]:
venues.head()

Name              Category postal_code
0  Oslo Kaffebar           Coffee Shop       10115
1       Petrarca    Italian Restaurant       10115
2    Schnitzelei  Schnitzel Restaurant       10115
3     Smart Deli   Japanese Restaurant       10115
4          Yarok    Falafel Restaurant       10115

We take a look at some venues which fall under the category 'Bar'.

In [13]:
venues.query("Category == 'Bar'").head()

Name Category postal_code
73               Melody Nelson Bar      Bar       10115
126                 Böse Buben Bar      Bar       10117
139  Meisterschueler Bar & Galerie      Bar       10117
221                      100 Gramm      Bar       10119
244       Lass uns Freunde bleiben      Bar       10119

Unfortunately not all bars in this dataframe are listed as bars, but for example as subcategories like 'Whisky Bar', 'Wine Bar', etc. Nevertheless we want to label these venues as 'Bars' and not treat them separately. The next code segment shows which subcategories of 'Bar' exist and counts the venues falling under these subcategories.

In [14]:
category_dataframe = venues.groupby('Category').count().sort_values('Name', ascending = False)
category_dataframe[category_dataframe.index.str.contains('Bar')]

Name  postal_code
Category                             
Bar                  154          154
Cocktail Bar          56           56
Wine Bar              29           29
Beer Bar              15           15
Hookah Bar            15           15
Dive Bar              12           12
Gay Bar               12           12
Hotel Bar             10           10
Salon / Barbershop     5            5
Whisky Bar             4            4
Sports Bar             4            4
Piano Bar              2            2
Beach Bar              2            2
Karaoke Bar            1            1
Juice Bar              1            1

Besides of 'Salon / Barbershop' all these categories can be considered as bars. Therefore all venues which fall under a category in the list above are simply labeled as 'Bar'. This is performed through:

In [15]:
bar_names_list = ['Bar','Cocktail Bar','Wine Bar',
                  'Hookah Bar','Beer Bar','Dive Bar',
                  'Hotel Bar','Gay Bar','Whisky Bar',
                  'Sports Bar','Juice Bar','Beach Bar',
                  'Piano Bar','Karaoke Bar']

for i in venues.index:
    if(venues.loc[i,'Category'] in bar_names_list):
        venues.at[i,'Category'] = 'Bar'

## 3. Methodology
### 3.1. Visualization of Query Results (Exploratory Analysis)

Since it's our aim to find a good model to predict the number of bars in the postal code regions, several plots of this variable are provided.

First the number of bars in each region is computed and printed (in descending order):

In [16]:
venues['nr_of_bars'] = (venues['Category'] == 'Bar').astype('int')
postal_code_bars = venues[['postal_code','nr_of_bars']].groupby('postal_code').sum().sort_values('nr_of_bars',ascending = False)
postal_code_bars

nr_of_bars
postal_code            
10999                18
12047                15
12049                11
10997                11
12045                10
13347                10
10405                10
10437                10
10245                10
10961                10
13357                 9
10117                 9
10119                 9
10967                 9
12043                 8
12053                 7
10557                 7
10777                 7
10439                 6
12055                 6
10243                 6
10623                 5
10787                 5
10115                 5
10551                 5
13353                 5
10435                 5
10247                 5
10785                 4
10965                 4
...                 ...
12309                 0
12347                 0
13051                 0
12689                 0
12687                 0
12685                 0
12683                 0
12679                 0
12629                 0
12627                 0
12623                 0
12621                 0
12619                 0
12589                 0
12559                 0
12557                 0
12527                 0
12526                 0
12524                 0
12489                 0
12487                 0
12459                 0
12439                 0
12437                 0
12359                 0
12357                 0
12355                 0
12351                 0
12349                 0
14199                 0

[190 rows x 1 columns]

The following code segments provides a geographical plot. The color of each postal code region gives the number of bars. A darker color corresponds to a higher number.

In [17]:
postal_code_bars.reset_index(inplace = True)

berlin_map = folium.Map(location = [berlin_lat, berlin_lng],
                        zoom_start = 10,
                        title = 'Berlin Postal Codes')

choropleth = folium.Choropleth(
    geo_data = berlin_geojson,
    data = postal_code_bars,
    columns = ['postal_code','nr_of_bars'],
    key_on = 'feature.properties.spatial_name',
    fill_color = 'YlOrRd',
    reset = True
).add_to(berlin_map)

choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['spatial_name'])
)

berlin_map

Finally a histogram is provided.

In [18]:
import matplotlib.pyplot as plt

n, bins, patches = plt.hist(postal_code_bars['nr_of_bars'],bins = 20, rwidth = 0.7)
plt.xlabel('number of bars')
plt.xticks(range(18))
plt.title('Histogram for number of bars')

plt.show()

<Figure size 640x480 with 1 Axes>

These tables and plots show that the bars were mostly found in the center regions of berlin (as one would expect).

### 3.2. Application of Neural Network (Machine Learning)

#### Preparation of Input Data

In this subsection the information in the dataframe are transformed to be used as an input of a Neural Network. Like in the previous examples of this course the number of venues in each category will be used as independent variable in the model.

The number of categories is relatively high compared to number of samples ( which is the number of postal code region: 190). To avoid overfitting only the most frequent categories are selected as independent variables. These categories are the following one:

In [19]:
top_20_categories = category_dataframe['Name'][0:20].index
top_20_categories

Index(['Supermarket', 'Café', 'Italian Restaurant', 'Hotel', 'Bar', 'Bakery',
       'German Restaurant', 'Bus Stop', 'Coffee Shop', 'Ice Cream Shop',
       'Vietnamese Restaurant', 'Park', 'Drugstore', 'Restaurant',
       'Pizza Place', 'Plaza', 'Gym / Fitness Center', 'Doner Restaurant',
       'Cocktail Bar', 'Asian Restaurant'],
      dtype='object', name='Category')

In [20]:
pd.DataFrame(category_dataframe['Name'][0:23])

Name
Category                   
Supermarket             317
Café                    292
Italian Restaurant      231
Hotel                   159
Bar                     154
Bakery                  153
German Restaurant       122
Bus Stop                122
Coffee Shop             121
Ice Cream Shop          116
Vietnamese Restaurant   103
Park                    101
Drugstore                89
Restaurant               78
Pizza Place              73
Plaza                    72
Gym / Fitness Center     65
Doner Restaurant         58
Cocktail Bar             56
Asian Restaurant         56
Tram Station             52
Burger Joint             49
Chinese Restaurant       48

The venues which belong to one of the categories above are saved in a new dataframe:

In [21]:
venues_top_20 = venues[venues['Category'].isin(top_20_categories)]

How many venues are left in total?

In [22]:
venues_top_20.shape

(2645, 4)

We apply the one hot encoding to the venues in the same way as in the previous part of the course and obtain a dataframe 'venues_grouped' which contains the independent (X) and the dependent variable (y).

In [23]:
# one hot encoding of venue Categories

venues_onehot = pd.get_dummies(venues_top_20[['Category']],
                               prefix = "",
                               prefix_sep = "")
venues_onehot['postal_code'] = venues_top_20['postal_code']

venues_grouped = venues_onehot.groupby('postal_code').sum()
venues_grouped.head()

Asian Restaurant  Bakery  Bar  Bus Stop  Café  Coffee Shop  \
postal_code                                                               
10115                       0       1    5         0     3            7   
10117                       0       0    9         0     3            2   
10119                       0       3    9         0     5            3   
10178                       1       0    0         0     1            4   
10179                       0       1    0         0     3            0   

             Doner Restaurant  Drugstore  German Restaurant  \
postal_code                                                   
10115                       0          1                  1   
10117                       0          1                  3   
10119                       0          0                  0   
10178                       0          0                  1   
10179                       0          1                  1   

             Gym / Fitness Center  Hotel  Ice Cream Shop  Italian Restaurant  \
postal_code                                                                    
10115                           0      4               2                   3   
10117                           0      8               0                   1   
10119                           0      4               3                  10   
10178                           1      3               2                   0   
10179                           1     10               0                   0   

             Park  Pizza Place  Plaza  Restaurant  Supermarket  \
postal_code                                                      
10115           0            0      0           4            1   
10117           0            1      3           2            0   
10119           1            3      1           1            0   
10178           0            0      1           2            0   
10179           0            0      1           0            0   

             Vietnamese Restaurant  
postal_code                         
10115                            2  
10117                            0  
10119                            5  
10178                            3  
10179                            1

In [24]:
X = venues_grouped.drop(['Bar'],axis = 1)
y = venues_grouped['Bar']
print(X.shape)
print(y.shape)

(189, 18)
(189,)


#### Building and Training the Model

The necessary input data was created above. Now it's time to set up the model. We use a neural network with one layer and the rectified linear unit (relu) as activation function. This model is very close to a linear model with the difference that no negative value will be predicted (the activation function is simply the identity with setting negative values to zero).

But first let's import the necessary packages:

In [61]:
from keras import Sequential, optimizers
from keras.layers import Dense, Activation

The neural network is defined as described above. Furthermore the optimizer, the learning rate and the loss function are specified. These hyperparameters are chosen heuristically for good results on this dataset (after trying several other hyperparameters).

In [62]:
model_nn = Sequential()
model_nn.add(Dense(1, activation = 'relu', input_dim = 18))

opt = optimizers.adam(lr = 0.04)

model_nn.compile(loss = "mae", optimizer = opt)

The model is compiled and can now be fitted to the dataset. Additionaly a seed is set to obtain reproducible results.

In [64]:
from numpy.random import seed
seed(1)
from tensorflow import set_random_seed
set_random_seed(2)

model_nn.fit(X,y, epochs = 80)

Epoch 1/80
189/189 [==============================] - 0s 573us/step - loss: 1.1916
Epoch 2/80
189/189 [==============================] - 0s 45us/step - loss: 1.0476
Epoch 3/80
189/189 [==============================] - 0s 41us/step - loss: 0.9811
Epoch 4/80
189/189 [==============================] - 0s 60us/step - loss: 0.9589
Epoch 5/80
189/189 [==============================] - 0s 24us/step - loss: 0.9318
Epoch 6/80
189/189 [==============================] - 0s 71us/step - loss: 0.8974
Epoch 7/80
189/189 [==============================] - 0s 37us/step - loss: 0.8796
Epoch 8/80
189/189 [==============================] - 0s 43us/step - loss: 0.8580
Epoch 9/80
189/189 [==============================] - 0s 26us/step - loss: 0.8440
Epoch 10/80
189/189 [==============================] - 0s 39us/step - loss: 0.8416
Epoch 11/80
189/189 [==============================] - 0s 35us/step - loss: 0.8271
Epoch 12/80
189/189 [==============================] - 0s 33us/step - loss: 0.8403
Epoch 13/80


The value of the loss function shows that after 80 iterations the mean absolute error (MAE) is about 0.73, which is still a pretty high error.

Nevertheless we compute the predicted number of bars in each region by this model.

In [65]:
y_pred_nn = model_nn.predict(X)

df_prediction = pd.DataFrame({'y':y})
df_prediction['y_pred_nn'] = y_pred_nn
df_prediction

y  y_pred_nn
postal_code               
10115         5  11.183410
10117         9   8.986917
10119         9   9.350433
10178         0   4.687673
10179         0   3.166107
10243         6   6.148130
10245        10  10.145160
10247         5   6.570948
10249         2   1.096555
10315         0   0.000000
10317         0   0.000000
10318         1   0.000000
10319         1   0.000000
10365         0   0.000000
10367         0   0.000000
10369         1   0.000000
10405        10   2.178155
10407         1   0.000000
10409         1   0.000000
10435         5   8.190502
10437        10  10.695435
10439         6   6.335176
10551         5   4.970119
10553         0   0.000000
10555         1   0.746458
10557         7   8.244853
10559         2   0.799555
10585         1   0.000000
10587         0   1.925662
10589         2   2.040788
...          ..        ...
13509         0   0.000000
13581         0   0.000000
13583         0   0.000000
13585         0   0.000000
13587         0   0.000000
13589         0   0.000000
13591         0   0.000000
13593         0   0.000000
13595         0   0.000000
13597         0   0.000000
13599         0   0.000000
13627         0   0.000000
13629         1   0.649233
14050         0   0.000000
14052         1   0.000000
14053         0   0.000000
14055         0   2.045283
14057         0   0.888073
14059         1   0.000000
14089         0   0.000000
14109         0   0.009716
14129         0   0.000000
14163         0   0.065928
14165         0   0.000000
14167         0   0.000000
14169         0   0.000000
14193         0   1.539294
14195         0   1.529616
14197         1   0.000000
14199         0   0.544717

[189 rows x 2 columns]

The five regions with the biggest difference of the predicted and the real value are:

In [66]:
df_prediction['y_diff'] = df_prediction['y_pred_nn'] - df_prediction['y']
df_prediction = df_prediction.sort_values('y_diff',ascending = False)

df_prediction.head()

y  y_pred_nn    y_diff
postal_code                        
10115        5  11.183410  6.183410
10178        0   4.687673  4.687673
10969        3   6.689893  3.689893
10435        5   8.190502  3.190502
10963        1   4.188982  3.188982

The difference of the predicted and the real number of bars of each region is plotted geographically in the next plot.

In [67]:
df_prediction.reset_index(inplace = True)

berlin_map = folium.Map(location = [berlin_lat, berlin_lng],
                        zoom_start = 10,
                        title = 'Berlin Postal Codes')

choropleth = folium.Choropleth(
    geo_data = berlin_geojson,
    data = df_prediction,
    columns = ['postal_code','y_diff'],
    key_on = 'feature.properties.spatial_name',
    fill_color = 'RdYlGn',
    reset = True
).add_to(berlin_map)

choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['spatial_name'])
)

berlin_map

The following code segments prints the weight matrix of the trained model (which is a vector in this case). It shows that the model expects more bars in a postal code region, if there are for example bakeries, Cafés, Coffee Shops, Doner Restaurants, Italian Restaurants, etc. On the other hand the model expects less bars if there are Asian Restaurants, Bus Stops, Gyms, Supermarkets, etc.

In [68]:
df_weights = pd.DataFrame({'venue_category':X.columns})
df_weights['coef'] = model_nn.layers[0].get_weights()[0]
df_weights.set_index('venue_category', inplace = True)
df_weights

coef
venue_category                 
Asian Restaurant      -0.471258
Bakery                -0.175684
Bus Stop              -2.578593
Café                   1.059286
Coffee Shop            1.648937
Doner Restaurant       0.522624
Drugstore             -0.222207
German Restaurant      0.013230
Gym / Fitness Center  -0.432473
Hotel                  0.151093
Ice Cream Shop        -0.113445
Italian Restaurant     0.179842
Park                   0.631692
Pizza Place            0.016916
Plaza                  0.992595
Restaurant            -0.263432
Supermarket           -0.782066
Vietnamese Restaurant -0.535420

### 4. Results

On the last map in the previous chapter we already visualized the difference of the predicted and the real number of bars for each region. In particular one can see the regions with the highest difference.

Now we take a look at the venues in these regions. Which venues are there and how many of them?

In [69]:
venues_grouped.loc[df_prediction.head()['postal_code']].T

postal_code            10115  10178  10969  10435  10963
Asian Restaurant           0      1      0      0      1
Bakery                     1      0      2      1      1
Bar                        5      0      3      5      1
Bus Stop                   0      0      0      0      0
Café                       3      1      2      5      3
Coffee Shop                7      4      3      2      1
Doner Restaurant           0      0      0      2      0
Drugstore                  1      0      0      0      0
German Restaurant          1      1      1      3      0
Gym / Fitness Center       0      1      1      1      1
Hotel                      4      3      3      1      4
Ice Cream Shop             2      2      0      1      0
Italian Restaurant         3      0      2      0      0
Park                       0      0      2      0      2
Pizza Place                0      0      1      3      0
Plaza                      0      1      0      1      0
Restaurant                 4      2      0      1      1
Supermarket                1      0      0      0      0
Vietnamese Restaurant      2      3      1      1      0

Indeed it is striking that the number of bars in these regions is relatively small compared to the number of other venues. For example in the region with the postal code 10115 there are i.e. 7 Coffee Shops and 5 Café's, but only 5 Bars.

### 5. Discussion

It is worth to mention that this analysis still has some weaknesses. The first one is that even in Berlin the list of venues which is found by the Foursquare API is not close to being complete. A lot of venues are simply not found. Of course other APIs with more venues provide more data and therefore would arguably yield more stable results. In particular for the above model there are 20 parameters fitted to just 190 observations. This is a rate of 190/20 roughly 10 observations per parameters, which is still quite low. Therefore there is good chance that the above model is overfitted. The most important action to eliminate this overfitting and build a better model simply more data is needed. Since we are restricted to the Foursquare API we remain which this conclusion in this analysis.

### 6. Conclusion

As it was described in the introduction we built a regression model which predicts the number of bars for each postal code region in Berlin and identified the regions with the highest difference of predicted and real number of bars. In the previous sub chapter (2.4.3.) the top five regions are listed. These regions have indeed a low number of bars compared to the number of other venues. 
